In [22]:
from __future__ import print_function
import matplotlib.pyplot as plt # librairie de plot
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import numpy as np

def un(x):
    return 1.0

# SIR Model and variation

The SIR model is the most basic model used in **epidemiology**. It was introduced in 1930 by Kermack and McKendrick in *A Contribution to the Mathematical Theory of Epidemics*.

The principle is to divide the population into epidemiological classes such as those susceptible to infection, those who are infectious, and those who have acquired immunity as a result of recovery.

## Model and theory

We consider three functions: susceptible peoples $S(t)$, infected peoples $I(t)$ and recovered peoples $R(t)$. The dynamic is described by

$$
\begin{align}
\dot{S}(t) & = -\beta \frac{S(t)I(t)}{N} \\
\dot{I}(t) & = \beta \frac{S(t)I(t)}{N} - \gamma I(t) \\
\dot{R}(t) & = \gamma I(t)
\end{align}
$$

with $N=S(t)+I(t)+R(t)$ the total population, $\beta$ the transmission date and $\gamma^{-1}$ the average duration of infection.

The transmission rate $\beta$ can be obtain as a product of **the probability of infection by contact** $\beta_p$ and **the average number of contact by day** $\beta_c$ . The first one depend of the disease mainly and the second one of the demography.


**Theorem (threshold theorem)"**:

*We define $\mathcal{R}_t = \mathcal{R}_0 \frac{S(t)}{N}$ with the reproduction number $\mathcal{R}_0=\frac{\beta}{\gamma}$.
If $\mathcal{R}_t>1$ the number of infected increase, if $\mathcal{R}_t<1$ the number of infected decrease.*

To obtain this result we write the equation on $I(t)$ on the following form

$$
\dot{I}(t) = \lambda I(t)
$$

with $\lambda= \gamma\left(\frac{\beta S(t)}{\gamma N}-1\right)$. The theory of ODE say that the solution is given by $I(t) = I(0)e^{\lambda t}$. If $\lambda<0$ we obtain a decreasing population in time.

**Corollary (epidemic/not epidemic)**:

*If $\mathcal{R}_0 S_0 >1$ there is epidemic, if $\mathcal{R}_0 S_0<1$ there is no epidemic.*


### Mathemical results

The previous result is very formal. We can prove the asympotitic behavior of the model with more rigourous arguments. 
Firstly we recall that $ S(t)+I(t)+R(t)=N$. So we can consider only $S(t)$ and $I(t)$.

We define the set $D=\left\{ S(t)\geq 0, I(t) \geq 0, S(t)+I(t) < N\right\}$. We can prove that the solution still always in the set if it is the case at the initial time.


**"Theorem (Asymptotic Behavior)"**:

We consider a trajectory $(S(t),I(t))\in D$. 
- if $\mathcal{R}_0 \leq 1$ then $lim_{t\rightarrow \infty }(S(t),I(t))=(N,0)$
- if $\mathcal{R}_0 \geq 1$ then $lim_{t\rightarrow \infty }(S(t),I(t))=\left(\frac{N}{\mathcal{R}_0},0\right)$

The idea is to prove, for each case, that the equilibrium point is stable and $D$ a stability domain. It can used Lyapunov theory.

It is also possible to prove that the system can be write as a **Poisson-system** (generalization of Hamiltonian one).

### Ways to mitigate a epidemic

We see on the model that the term which create new infections is :

$$
\beta_p \beta_c I(t)S(t)
$$

Possible solution to limit the force of this term:

- decrease $S(t)$, It is strategy of Vaccin. Indeed we limit the population without protection agains the disease.
- decrease $I(t)$, It is the strategy of test+Quanrantine. The quarantine isolate a portion of the population. I(t).
- decrease $\beta_c$, It is the strategy  of social distancing, lockdown, school closure etc.
- decrease $\beta_p$, It is the strategy of Mask, washing hands etc.

## Numerical scheme for SIR

Now we propose to solve this model. For that we consider a serie of time $t_n = n \Delta t$. We note $S_n\approx S(t_n)$ (idem for $I_n$ and $R_n$). After time discretization (forward Euler scheme) we obtain the following algorithm:

$$
\begin{align}
S_{n+1} & = S_n -\Delta t\beta \frac{S_n I_n}{N} \\
I_{n+1} & = I_n +\Delta t\beta \frac{S_n I_n}{N} - \gamma I_n \\
R_{n+1} & = R_n +\Delta t\gamma I_n \\
\end{align}
$$

In [25]:
class SIR:
    
    def __init__(self,S0,I0):
        self.S = [S0];  self.I = [I0]; self.R = [0.0]
        self.N = [self.S[-1] + self.I[-1] +self.R[-1]]
        self.Rt = []
    
        self.k1=np.zeros(4,float)
        self.xn=np.zeros(4,float)
        self.xnp=np.zeros(4,float)
        
    def push_Rt(self,R0):
        self.Rt.append(R0*self.S[-1]/self.N[-1])
        
    def updateN(self):
        self.N[-1]=self.S[-1]+self.I[-1]+self.R[-1]
        
    def push_list_to_n(self):
        self.xn[0:4]=[self.S[-1],self.I[-1],self.R[-1],self.N[-1]]
    
    def update(self,vp,v1,v2,dt,beta,gamma):
            
        vp[0] = v1[0]- dt*beta*v2[0]*v2[1]/v2[3] 
        vp[1] = v1[1]+ dt*beta*v2[0]*v2[1]/v2[3] -dt*gamma*v2[1]
        vp[2] = v1[2]+ dt*gamma*v2[1]
        
        vp[3] = vp[0]+vp[1]+vp[2]
        
    def push_np_to_list(self):     
        self.S.append(self.xnp[0]); self.I.append(self.xnp[1]);  
        self.R.append(self.xnp[2]); self.N.append(self.xnp[3])

In [23]:
def SIR_model(S0=999,I0=1,beta=0.7,gamma=0.25,ft=50,order="1"):
    m = SIR(S0,I0)
    R0 = beta/gamma
    m.push_Rt(R0)
    times =[0.0]; dt = 1.0
    
    while times[-1]<ft:
        m.push_list_to_n()
        
        if int(order)==1:
            m.update(m.xnp,m.xn,m.xn,dt,beta,gamma)
        else:
            m.update(m.k1,m.xn,m.xn,0.5*dt,beta,gamma)
            m.update(m.xnp,m.xn,m.k1,dt,beta,gamma)
        m.push_np_to_list()
        m.push_Rt(R0)
        times.append(times[-1]+dt) 
        
    plt.figure(figsize=(10,8))
    ax1 =plt.subplot(221)
    ax1.plot(times, m.N, 'r--', label="Tot population") 
    ax1.plot(times, m.R, 'g--', label="Recovered") 
    ax1.legend()

    ax2 =plt.subplot(222)
    un = np.ones(len(times))
    ax2.plot(times, m.Rt, 'cyan', label="Rt")
    ax2.plot(times, un, 'r--')
    ax2.legend()
    
    ax3 = plt.subplot(212)  
    ax3.plot(times, m.S, label='suceptible')
    ax3.plot(times, m.I, label='infected')
    ax3.legend()

## Numerical results for SIR

In [26]:
S0 = widgets.IntText(value=100000,description="S0")
I0 = widgets.IntText(value=1,description="I0")
b1 = widgets.HBox([S0,I0])

beta = widgets.FloatSlider(value=0.7,min=0.01,max=1.0,step=0.02,description="beta")
gamma = widgets.FloatSlider(value=0.3,min=0.01,max=1.0,step=0.02,description="gamma")
b2 = widgets.HBox([beta,gamma])

order = widgets.RadioButtons(options=['1','2'],value='1',description="order:")
ft = widgets.IntText(value=80,description="Final time")
b3 = widgets.HBox([order,ft])

ui= widgets.VBox([b1,b2,b3])
out = widgets.interactive_output(SIR_model, {'S0': S0, 'I0': I0, 'beta': beta, 'gamma': gamma,\
                                              "ft": ft, "order":order})


In [27]:
display(ui,out)

Output(outputs=({'output_type': 'display_data', 'data': {'text/plain': '<Figure size 720x576 with 3 Axes>', 'i…

## SIRS model death/birth process 

This model is similar to the previous one but we add three phenomena. We consider:

- the immunity only lasts for a limited time,
- there are birth/death in the population

We consider three functions: suceptible peoples $S(t)$, infectious peoples $I(t)$ and retired peoples $R(t)$. The dynamic is described by

$$
\begin{align}
\dot{S}(t) & = -\beta \frac{S(t)I(t)}{N(t)} + \lambda R(t) - \tau_m S(t) + \tau_n (S(t)+I(t)+R(t))  \\
\dot{I}(t) & = \beta \frac{S(t)I(t)}{N(t)} - \gamma I(t) - \tau_m I(t) \\
\dot{R}(t) & = \gamma I(t) - \tau_m R(t) - \lambda R(t)
\end{align}
$$

with $N(t)=S(t)+I(t)+R(t)$ the total population with $\lambda^{-1}$ the average duration of the immunity.

**Theorem (threshold theorem)"**:

*We define $\mathcal{R}_t = \mathcal{R}_0 S_n$ with the reproduction number $\mathcal{R}_0=\frac{\beta}{\gamma+ \tau_m}$.
If $\mathcal{R}_t>1$ the number of infected increase, if $\mathcal{R}_t<1$ the number of infected decrease.*

### Mathemical results

In the case $\tau_m=\tau_b$ we have that $ S(t)+I(t)+R(t)=N$. So we can consider only $S(t)$ and $I(t)$.

We define the set $D=\left\{ S(t)\geq 0, I(t) \geq 0, S(t)+I(t) < N\right\}$. We can prove that the solution still always in the set if it is the case at the initial time.


**"Theorem (Asymptotic Behavior)"**:

For $\lambda= 0$, We consider a trajectory $(S(t),I(t))\in D$. 
- if $\mathcal{R}_0 \leq 1$ then $lim_{t\rightarrow \infty }(S(t),I(t))=(N,0)$
- if $\mathcal{R}_0 \geq 1$ then $lim_{t\rightarrow \infty }(S(t),I(t))=\left(\frac{N}{\mathcal{R}_0},\frac{\tau}{\tau+\gamma}\left(1-\frac{1}{\mathcal{R}_0}\right)N\right)$


## Numerical scheme for SIRS

We use the same scheme in time as before

In [28]:
def SIRSdeath_model(S0=9999,I0=1,beta=0.7,gamma=0.3,lamb=0.02,taum=0.00,taun=0.00,ft=200):
    S = [S0]; I = [I0]; R = [0.0]; N =[S0+I0]
    Rt = [beta/gamma*S[-1]/N[-1]]
    times =[0.0]
    dt = 0.1
    
    while times[-1]<ft:
        Snp = S[-1] - dt*beta*S[-1]*I[-1]/N[-1] +dt*lamb*R[-1] -dt*taum*S[-1]+dt*taun*N[-1]
        Inp = I[-1] + dt*beta*S[-1]*I[-1]/N[-1] -dt*gamma*I[-1]-dt*taum*I[-1]
        Rnp = R[-1] + dt*gamma*I[-1]-dt*lamb*R[-1]-dt*taum*R[-1]
        times.append(times[-1]+dt)
        S.append(Snp)
        I.append(Inp)
        R.append(Rnp)
        N.append(Snp+Inp+Rnp)
        Rt.append((beta/gamma)*(Snp/N[-1]))
        
    plt.figure(figsize=(10,8))
    ax1 =plt.subplot(221)
    ax1.plot(times, I, label='infected')
    ax1.legend()

    ax2 =plt.subplot(222)
    un = np.ones(len(times))
    ax2.plot(times, Rt, 'cyan', label="Rt")
    ax2.plot(times, un, 'r--')
    ax2.legend()
    
    ax3 = plt.subplot(212)
    ax3.margins(0, 0)  
    ax3.plot(times, N, 'r--', label="Tot population")
    ax3.plot(times, S, 'b--', label='suceptible')
    ax3.plot(times, R, 'g--', label="Recovered") 
    ax3.legend()

## Numerical results for SIRS

In [29]:
S0 = widgets.IntText(value=100000,description="S0")
I0 = widgets.IntText(value=1,description="I0")
b1 = widgets.HBox([S0,I0])

beta = widgets.FloatSlider(value=0.7,min=0.01,max=1.0,step=0.02,description="Beta:")
gamma = widgets.FloatSlider(value=0.3,min=0.01,max=1.0,step=0.02,description="Gamma:")
lamb = widgets.FloatSlider(value=0.0,min=0.00,max=0.1,step=0.005,description="Lambda:")
b2 = widgets.HBox([beta,gamma,lamb])

taum = widgets.FloatText(value=0.0,description="Tau death:")
taun = widgets.FloatText(value=0.0, description="Tau neworn:")
ft = widgets.IntText(value=200, description="Final time:")
b3 = widgets.HBox([taum,taun,ft])

ui= widgets.VBox([b1,b2,b3])
out = widgets.interactive_output(SIRSdeath_model, {'S0': S0, 'I0': I0, 'beta': beta, 'gamma': gamma,\
                                              'lamb': lamb, "taum": taum, "taun":taun,\
                                             "ft": ft})

In [30]:
display(ui,out)

Output(outputs=({'output_type': 'display_data', 'data': {'text/plain': '<Figure size 720x576 with 3 Axes>', 'i…

## SIR model death/birth process  and Hospital

Here we add the possibility of the patient to be hospitalized. It can be interesting to see the pressure of the disease on the healthcare system.

We consider four functions: suceptible peoples $S(t)$, infectious peoples $I(t)$, hospitalized peoples $H(t)$ and retired peoples $R(t)$. The dynamic is described by

$$
\begin{align}
\dot{S}(t) & = -\beta \frac{S(t)I(t)}{N(t)} - \tau_m S(t) + \tau_n (S(t)+I(t)+R(t))  \\
\dot{I}(t) & = \beta \frac{S(t)I(t)}{N(t)} - \gamma I(t) -  - \tau_m I(t) \\
\dot{H}(t) & = \gamma \delta  I(t) - \lambda H(t) - \tau_m H(t) \\
\dot{R}(t) & = \gamma (1-\delta)I(t) + \lambda H(t) - \tau_m R(t)
\end{align}
$$

with $N(t)=S(t)+I(t)+R(t)$ the total population, $\delta$ the probability to be hospitalized and $\lambda^{-1}$ the average time at hospital. 

**Theorem (threshold theorem)"**:

*We define $\mathcal{R}_t = \mathcal{R}_0 \frac{S(t)}{N}$ with the reproduction number $\mathcal{R}_0=\frac{\beta}{\gamma+ \tau_m}$.
If $\mathcal{R}_t>1$ the number of infected increase, if $\mathcal{R}_t<1$ the number of infected decrease.*

**Corollary (epidemic/not epidemic)**:

*If $\mathcal{R}_0 S_0 >1$ there is epidemic, if $\mathcal{R}_0 S_0<1$ there is no epidemic.*

## Numerical scheme for SIRH

We use the same scheme in time as before

In [33]:
def SIHRdeath_model(S0=10000,I0=1,beta=0.7,gamma=0.3,delta=0.1,lamb=0.1,taum=0.0,taun=0.00,ft=100):
    S = [S0]; I = [I0]; H=[0.0]; R = [0.0]; N =[S0+I0]
    Rt = [beta/gamma*S[-1]/N[-1]]
    times =[0.0]; dt = 0.1
    
    while times[-1]<ft:
        Snp = S[-1] - dt*beta*S[-1]*I[-1]/N[-1] -dt*taum*S[-1]+dt*taun*N[-1]
        Inp = I[-1] + dt*beta*S[-1]*I[-1]/N[-1] -dt*gamma*I[-1]-dt*taum*I[-1]
        Hnp = H[-1] + dt*gamma*delta*I[-1] -dt*lamb*H[-1] -dt*taum*H[-1]
        Rnp = R[-1] + dt*gamma*(1.0-delta)*I[-1] + dt*lamb*H[-1] -dt*taum*R[-1]
        times.append(times[-1]+dt)
        S.append(Snp)
        I.append(Inp)
        H.append(Hnp)
        R.append(Rnp)
        N.append(Snp+Inp+Hnp+Rnp)
        Rt.append((beta/gamma)*(Snp/N[-1]))
        
    plt.figure(figsize=(10,8))
    ax1 =plt.subplot(221)
    ax1.plot(times, N, 'r--', label="Tot pol") 
    ax1.plot(times, S, 'b--', label='suceptible')
    ax1.plot(times, R, 'g--', label="Recovered") 
    ax1.legend()
    
    ax2 =plt.subplot(222)
    un = np.ones(len(times))
    ax2.plot(times, Rt, 'c', label="Rt")
    ax2.plot(times, un, 'r--')
    ax2.legend()
    
    ax3 = plt.subplot(212)
    ax3.plot(times, I, label='infected')
    ax3.plot(times, H, label='Hospitalized')
    ax3.legend()   

## Numerical results for SIRH

In [34]:
S0 = widgets.IntText(value=100000,description="S0")
I0 = widgets.IntText(value=1,description="I0")
b1 = widgets.HBox([S0,I0])

beta = widgets.FloatSlider(value=0.7,min=0.01,max=1.0,step=0.02,description="Beta:")
gamma = widgets.FloatSlider(value=0.3,min=0.01,max=1.0,step=0.02,description="Gamma:")
lamb = widgets.FloatSlider(value=0.1,min=0.02,max=1.0,step=0.005,description="Lambda:")
delta = widgets.FloatSlider(value=0.2,min=0.00,max=1.0,step=0.05,description="Delta:")
b2 = widgets.HBox([beta,gamma])
b3 = widgets.HBox([lamb,delta])

taum = widgets.FloatText(value=0.0,description="Tau death:")
taun = widgets.FloatText(value=0.0, description="Tau neworn:")
ft = widgets.IntText(value=200, description="Final time:")
b4 = widgets.HBox([taum,taun,ft])

ui= widgets.VBox([b1,b2,b3,b4])
out = widgets.interactive_output(SIHRdeath_model, {'S0': S0, 'I0': I0, 'beta': beta, 'gamma': gamma,\
                                              'delta':delta, 'lamb': lamb, "taum": taum, "taun":taun,\
                                             "ft": ft})

In [35]:
display(ui,out)

Output(outputs=({'output_type': 'display_data', 'data': {'text/plain': '<Figure size 720x576 with 3 Axes>', 'i…